Where to find forms: https://docs.google.com/spreadsheets/d/1-L8rIMTMQGPrmdFsa70k85RWJaZCurad_zug7qFHS68/edit#gid=130175332

# Load Libraries

In [2]:
import urllib.request, json 
from urllib.request import urlopen
import re
from bs4 import BeautifulSoup
import pandas as pd
import time
from datetime import date
import os
from os import walk
import os.path
from os import path
import uuid

import re
import random

import numpy as np

import hashlib

import requests

from urllib.request import Request, urlopen
from urllib.parse import quote

#!pip install PyPDF2
import PyPDF2

from io import StringIO # https://stackoverflow.com/a/18284900
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.converter import TextConverter
from pdfminer.layout import LAParams
from pdfminer.pdfpage import PDFPage

from contextlib import contextmanager
import threading
import _thread

class TimeoutException(Exception): pass
@contextmanager
def time_limit(seconds):
    timer = threading.Timer(seconds, lambda: _thread.interrupt_main())
    timer.start()
    try:
        yield
    except KeyboardInterrupt:
        raise TimeoutException("Timed out.")
    finally:
        # if the action ends in specified time, timer is canceled
        timer.cancel()


def convert(fname, pages=None):
    if not pages:
        pagenums = set()
    else:
        pagenums = set(pages)

    output = StringIO()
    manager = PDFResourceManager()
    converter = TextConverter(manager, output, laparams=LAParams())
    interpreter = PDFPageInterpreter(manager, converter)

    infile = open(fname, 'rb') # python three change
    for page in PDFPage.get_pages(infile, pagenums):
        interpreter.process_page(page)
    infile.close()
    converter.close()
    text = output.getvalue()
    output.close
    return text
   
def download_pdf(url,path,filename):
    
    global csv_path
    
    if not os.path.exists(path):
        os.makedirs(path)
    
    try:
        filename = path+filename

        f = requests.get(url, stream=True, headers={'User-agent': 'Mozilla/5.0'})

        with open(filename, "wb") as code:
            #code.write(f.read())
            code.write(f.content)

        return convert(filename)
    except:
        return "error"
    
def hashme(w):
    h = hashlib.md5(w.encode('utf-8'))
    return h.hexdigest()

def get_soup(url):
    if re.search("^file:\/\/",url):
        try:
            with open(re.findall("file:\/\/(.*)",url)[0], 'r') as file:
                page = file.read()
            soup = BeautifulSoup(page)
            return soup
        except:
            print("Error reading file:",re.findall("file:\/\/(.*)",url)[0])
    else:
        try:
            try:
                with time_limit(10):
                    with urllib.request.urlopen(urllib.request.Request(url, headers={'User-agent': 'Mozilla/5.0'}), timeout=15) as url:
                        try:
                            content = url.read().decode()
                        except:
                            content = url.read().decode("iso-8859-1")

                    soup = BeautifulSoup(content)
                    return soup
            except TimeoutException as e:
                print("Timed out!")
                return None
        except:
            print("Error Reading Page!!!")
            return None
    
def pars_link(this_url,href):
    
    if (this_url.split("/")[-1] == "") and (re.search("\.|\?",this_url.split("/")[-1])):
        this_url = this_url.replace(this_url.split("/")[-1],"")

    if this_url[-1]!="/":
        this_url += "/"

    http = re.findall("(https?://)([^/]*)",this_url)[0][0]
    domain = re.findall("(https?://)([^/]*)",this_url)[0][1] 

    if (len(href)>0) & (re.search("^http",href)==None):
        if href[0]=="/":
            output = http + domain + href
        elif href[0]=="#":
            output = "error"
        elif re.search("^javascript",href):
            output = "error"
        else:
            output = this_url + href
    else:
        output = href
            
    #print(output)
    return output

def get_links(jurisdiction,url,regex_form,regex_link,goto_depth=0,depth=0):
    
    global min_wait, max_wait, visited_df
    
    print("\nChecking",url)
    soup = get_soup(url)
    
    if soup!=None:

        files_df = pd.DataFrame([],columns=["jurisdiction","source","group","title","url","filename","downloaded"])
        links_df = pd.DataFrame()

        if re.search("^file:\/\/",url):
            source = re.findall("file:\/\/\.\.\/data\/state_forms\/_saved_html\/(.*)\.html?$",url)[0]
            source = re.sub("\\\\","/",source)
            url = "https://" + source
            #print(url)
        else:
            source = re.findall("(https?://)([^/]*)",url)[0][1]

        links = []

        for a in soup.find_all('a', href=True):

            for reg in regex_form:
                href = a['href']    
                href = pars_link(url,href)
                if re.findall(reg,href,re.IGNORECASE):
                    
                    #try:
                    file_id = hashme(href)
                    group = np.nan
                    if len(a.contents)>0:
                        title = a.contents[0].getText()
                    else:
                        title = "UNKNOWN"
                    form_url = href
                    filename = re.findall(reg,href,re.IGNORECASE)[0]
                    downloaded = 0

                    files_df = pd.concat([files_df, pd.DataFrame([[jurisdiction,source,group,title,form_url,filename,downloaded]],columns=["jurisdiction","source","group","title","url","filename","downloaded"],index=[file_id])])            
                    #except:
                    #    print("Error parsing link to form!")

        files_df = files_df[~files_df.index.duplicated(keep='first')]
        print(len(files_df),"possible forms")
        
        print("Depth",depth)
        for a in soup.find_all('a', href=True):
            
            for reg in regex_link:
                href = a['href']    
                href = pars_link(url,href)
                if (href!="error") and (re.findall(reg,href,re.IGNORECASE)):
                    #print(href,goto_depth,depth)
                    if ((href not in files_df["url"].values) & (goto_depth > depth)):
                        links_df = pd.concat([links_df, pd.DataFrame([[href,0]],columns=["url","visited"])])

        links_df = links_df.drop_duplicates()
        print(len(links_df),"links to follow")
        #display(links_df)

        if (len(links_df)>0):
            new_depth = depth+1
            for link in links_df["url"]:
                if (link not in visited_df["link"].values):
                    print("trying link...")
                    time.sleep(random.uniform(min_wait, max_wait))
                    files_df = pd.concat([files_df,get_links(jurisdiction,link,regex_form,regex_link,goto_depth=goto_depth,depth=new_depth)])
                    visited_df = pd.concat([visited_df,pd.DataFrame([[link]],columns=["link"])])
                
        files_df = files_df[~files_df.index.duplicated(keep='first')]
        print(len(files_df),"possible forms this run\n")                
        return files_df
    
    else:
        print("Error reading",url)
        return pd.DataFrame()

min_wait = 0
max_wait = 1

csv_path = "../data/state_forms/"

In [3]:
try:
    forms_df = pd.read_csv(csv_path+"form_data.csv", index_col=0, encoding="utf-8")
except: 
    forms_df = pd.DataFrame([],columns=["id","jurisdiction","source","group","title","url","filename","downloaded"])
    forms_df.set_index(["id"], inplace = True, drop = True)
    
print("Downloaded:",len(forms_df[forms_df["downloaded"]==1]))
print("Pending:",len(forms_df[forms_df["downloaded"]==0]))
print("All Entries:",len(forms_df))

forms_df.head()

Downloaded: 0
Pending: 0
All Entries: 0


Empty DataFrame
Columns: [jurisdiction, source, group, title, url, filename, downloaded]
Index: []

## Scrape Sites

In [4]:
states = [
    
     {"regex_form":["/download$","([^\/]*\.pdf)"],"regex_link":["\/lists\/"],"goto_depth":1,"jurisdiction":"MA","url":"https://www.mass.gov/guides/court-forms-by-topic"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"UT","url":"https://legacy.utcourts.gov/forms/"}   
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["forms\/"],"goto_depth":1,"jurisdiction":"IL","url":"https://www.illinoiscourts.gov/documents-and-forms/approved-forms/"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/forms\/","\/court_rules\/"],"goto_depth":1,"jurisdiction":"WA","url":"https://www.courts.wa.gov/forms/"}    
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":1,"jurisdiction":"AL","url":"https://eforms.alacourt.gov"}    
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":1,"jurisdiction":"CT","url":"https://www.jud.ct.gov/webforms/"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"ID","url":"https://courtselfhelp.idaho.gov/Forms"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/forms\/"],"goto_depth":1,"jurisdiction":"NV","url":"https://selfhelp.nvcourts.gov/forms?enter=1"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"AK","url":"https://courts.alaska.gov/forms/index.htm"}
    ,{"regex_form":["\?Form=(.*)"],"regex_link":["\/Forms\/"],"goto_depth":2,"jurisdiction":"CO","url":"https://www.courts.state.co.us/Forms/Index.cfm"}    
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/form"],"goto_depth":1,"jurisdiction":"HI","url":"https://www.courts.state.hi.us/self-help/courts/forms/court_forms"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"AR","url":"https://www.arcourts.gov/forms-and-publications/court-forms"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"LA","url":"https://www.lsba.org/Public/FindLegalHelp/Forms.aspx"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MS","url":"https://courts.ms.gov/mec/Mec-forms.php"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/forms\/"],"goto_depth":1,"jurisdiction":"MT","url":"https://courts.mt.gov/forms/"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/legal-self-help\/"],"goto_depth":2,"jurisdiction":"ND","url":"https://www.ndcourts.gov/legal-self-help"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["forms","erpo"],"goto_depth":1,"jurisdiction":"NY","url":"https://www.nycourts.gov/forms/"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/all-forms\/"],"goto_depth":1,"jurisdiction":"OH","url":"https://www.supremecourt.ohio.gov/forms/all-forms/"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["form"],"goto_depth":1,"jurisdiction":"OK","url":"https://www.oscn.net/static/forms/start.asp"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":1,"jurisdiction":"PA","url":"https://www.pacourts.us/forms"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":1,"jurisdiction":"SD","url":"https://ujslawhelp.sd.gov/onlineforms.aspx"}    
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":1,"jurisdiction":"TN","url":"https://www.tncourts.gov/node/707185"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":1,"jurisdiction":"WV","url":"http://www.courtswv.gov/legal-community/court-forms.html"}
    ,{"regex_form":["\/download$"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"IA","url":"file://../data/state_forms/_saved_html/www.iowacourts.gov\\for-the-public\\court-forms.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"RI","url":"file://../data/state_forms/_saved_html/www.courts.ri.gov\\PublicResources\\forms\\Pages\\default.aspx.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"GA","url":"https://georgiacourts.gov/probate/standard-forms/"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"GA","url":"https://georgiacourts.gov/a2j/self-help-resources-highlighted-by-a2j/georgia-divorce-videos-and-forms/"}

    # Issue with depth > 2
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/legal-forms\/"],"goto_depth":3,"jurisdiction":"KS","url":"https://www.kansasjudicialcouncil.org/legal-forms"}  
    
    # There's more FL below
    ,{"regex_form":["\/showpublisheddocument\/"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"FL","url":"https://www.leeclerk.org/services/forms-library"}
    
    # The following regex is over inclusive
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":1,"jurisdiction":"TX","url":"https://www.txcourts.gov/rules-forms/forms/"}
    ## Guide and File Froms,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"TX","url":"https://selfhelp.efiletexas.gov/SRL"}
    
    # The following regex is over inclusive
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":2,"jurisdiction":"OR","url":"https://www.courts.oregon.gov/forms/Pages/default.aspx"}
    
    # ------ 

    # there are a bunch of zip files here?????
    # Oh, I went back and now they're password protected!!!
    # NOTE: some GA forms are above
    #,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"GA","url":"https://georgiacourts.gov/statecourt/state-court-behind-the-bench/state-court-forms/"}
    
    ### come back to ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"IN","url":"https://www.in.gov/courts/selfservice/"}
    
    ### Need to filter on text/name of href ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MO","url":"https://www.courts.mo.gov/page.jsp?id=103116"}

    ## all js ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"NM","url":"https://www.nmcourts.gov/self-help/forms/"}
    
    ## All Word Files?,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"AZ","url":"https://www.azcourts.gov/selfservicecenter/forms"}
    
    ## Read from HTML 
       
    ## save as htmt a lot of pages ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"NH","url":"https://www.courts.nh.gov/resources/forms-and-fees"}

    # Pull from local HTML because the page is dynamicly rendered
    # - Prepend `file://` to the "url" with what follows being the relative address of an html file
    # - When naming the file, replace any `/` in the url with `\`
    # - To keep track of pages with different content, but the same URL, you can append a `\?p=1` et al 
    
    ,{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=1.html"}    
    ,{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=2.html"}    
    ,{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=3.html"}    
    ,{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=4.html"}    
    ,{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=5.html"}    
    ,{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=6.html"}    
    ,{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=7.html"}    
    ,{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=8.html"}    
    
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"SC","url":"file://../data/state_forms/_saved_html/www.sccourts.org\\forms\\searchType.cfm.html"}
    
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"NJ","url":"file://../data/state_forms/_saved_html/www.njcourts.gov\\self-help\\forms?page=37.html"}
       
    
    # page dynamicly loads data
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"KY","url":"file://../data/state_forms/_saved_html/kycourts.gov\\Legal-Forms\\Pages\\default.aspx.html"}
    
    # page dynamicly loads data
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"ME","url":"file://../data/state_forms/_saved_html/mjbportal.courts.maine.gov/screen01.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"ME","url":"file://../data/state_forms/_saved_html/mjbportal.courts.maine.gov/screen02.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"ME","url":"file://../data/state_forms/_saved_html/mjbportal.courts.maine.gov/screen03.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"ME","url":"file://../data/state_forms/_saved_html/mjbportal.courts.maine.gov/screen04.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"ME","url":"file://../data/state_forms/_saved_html/mjbportal.courts.maine.gov/screen05.html"}

    # page dynamicly loads data
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/Abortion-Waiver.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/adoptions-court-forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/Alternative-dispute-res.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/appeals.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/case-evaluation.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/civil-infraction.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/claim-and-delivery.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/Collections-Forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/commitment-testing-ID.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/conservatorship-protected-individuals.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/Criminal-disposition-forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/criminal-felony-forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/Domestic-Relations.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/emancipation.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/Estates-Trusts.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/forfeiture.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/forms-criminal-misdemeanor.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/garnishment.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/General-Civil-forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/general-use.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/guardianship.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/juvenile-designated-forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/juvenile-guardianship-forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/juvenile-proceedings.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/LTLC-forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/MH-Forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/Mortgage-foreclosure.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/motor-vehicle-offenses-forms.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/name-change.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/Offender-Registration.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/PPO.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/probation.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/safe-delivery-newborn.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/small-claims.html"}
    ,{"regex_form":["strFormNumber=(.*$)","([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MI","url":"file://../data/state_forms/_saved_html/www.courts.michigan.gov/young-adult-foster-care-forms.html"}
    
    
    # individual results pages don't resolve
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p1.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p2.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p3.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p4.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p5.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p6.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p7.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p8.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p9.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p10.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p11.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p12.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p13.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p14.html"}
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"MD","url":"file://../data/state_forms/_saved_html/www.courts.state.md.us\\courtforms\\p15.html"}
    
    # page dynamicly loads data
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DC","url":"file://../data/state_forms/_saved_html/www.dccourts.gov\\services\\forms.html"}
    
    # had to open and re-save html files to utf-8
    ,{"regex_form":["jirc_complaint_form\.pdf","selfev2\.pdf"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VA","url":"file://../data/state_forms/_saved_html/www.vacourts.gov\\forms\\home.html.html"}                
    ,{"regex_form":[".*form.*\.pdf"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VA","url":"file://../data/state_forms/_saved_html/www.vacourts.gov\\courtadmin\\aoc\\djs\\programs\\jsc\\forms\\home.html.html"}                
    ,{"regex_form":[".*form.*\.pdf"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VA","url":"file://../data/state_forms/_saved_html/www.vacourts.gov\\courts\\cav\\forms.html.html"}                
    ,{"regex_form":[".*form.*\.pdf"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VA","url":"file://../data/state_forms/_saved_html/www.vacourts.gov\\courts\\scv\\forms.html.html"}                
    ,{"regex_form":[".*form.*\.pdf"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VA","url":"file://../data/state_forms/_saved_html/www.vacourts.gov\\forms\\circuit\\home.html.html"}                
    ,{"regex_form":[".*form.*\.pdf"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VA","url":"file://../data/state_forms/_saved_html/www.vacourts.gov\\forms\\district\\home.html.html"}                
    ,{"regex_form":[".*form.*\.pdf"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VA","url":"file://../data/state_forms/_saved_html/www.vacourts.gov\\forms\\district\\jdr.html.html"}                
    ,{"regex_form":[".*form.*\.pdf"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VA","url":"file://../data/state_forms/_saved_html/www.vacourts.gov\\forms\\home.html.html"}                

    # had to open and re-save html files to utf-8
    ,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"WY","url":"file://../data/state_forms/_saved_html/www.courts.state.wy.us\\legal-assistance-and-forms\\court-self-help-forms.html"}
    
]

## Loop through Pages

for i in range(1, 44, 1):
    # is a search page, loop through all 43 pages
    states.append({"regex_form":["([^\/]*\.pdf)"],"regex_link":["GetForms"],"goto_depth":1,"jurisdiction":"MN","url":"https://www.mncourts.gov/GetForms.aspx?c={}".format(i)})

for i in range(0, 4):
    # is a search page, loop through all 4 (0-3, as it's zero indexed)
    states.append({"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"NE","url":"https://supremecourt.nebraska.gov/forms?page={}".format(i)})    

for i in range(1, 3):
    # is a search page, loop through all 2 (1-2, as it's NOT zero indexed)
    states.append({"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"WI","url":"https://www.wicourts.gov/forms1/circuit/ccform.jsp?page={}&FormName=&FormNumber=&beg_date=&end_date=&StatuteCite=&Category=&Language=en+&Format=2&Submit=Search".format(i)})       

for i in range(0, 16):
    # is a search page, loop through all 16 (0-15, as it's zero indexed)    
    # pulled from iframe at https://www.courts.ca.gov/forms.htm
    states.append({"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"CA","url":"https://selfhelp.courts.ca.gov/find-forms/all?page={}".format(i)})    
    
for i in range(0, 35):
    # is a search page, loop through all 35 (0-34, as it's zero indexed)
    states.append({"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"VT","url":"https://www.vermontjudiciary.org/forms-library?search_api_fulltext=&page={}".format(i)})       
    
for i in range(0, 200, 50):
    # is a search page, loop through all 4 pages (uses offset instrad of page)
    # result page from https://www.flcourts.gov/Resources-Services/Office-of-Family-Courts/Family-Courts/Family-Law-Forms
    states.append({"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"FL","url":"https://www.flcourts.gov/search/form/?sort=form/number%20asc,%20form/date%20desc&view=embed_custom&searchtype=form&limit=50&query=&offset={}".format(i)})
    #print(i)    
    #,{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"FL","url":"https://help.flcourts.org/Get-Started/Find-a-Form"}
    
for i in range(0, 51):
    # is a search page, loop through all 52 (0-51, as it's zero indexed)
    # result page from 
    states.append({"regex_form":["([^\/]*\.pdf)"],"regex_link":["documents\/forms\/"],"goto_depth":1,"jurisdiction":"NC","url":"https://www.nccourts.gov/documents/forms?field_form_type_target_id=All&field_language_target_id=93&page={}".format(i)})
    

## Test

In [148]:
states = []
for i in range(1, 44, 1):
    # is a search page, loop through all 4 pages (uses offset instrad of page)
    # result page from https://www.courts.state.md.us/courtforms?forms%5B0%5D=languages%3A59&search_api_fulltext=&field_last_revised%5Bmin%5D=&field_last_revised%5Bmax%5D=&filename_1=&sort_bef_combine=title_ASC&sort_by=title&sort_order=ASC&forms%5B0%5D=languages%3A59&page={}
    states.append({"regex_form":["([^\/]*\.pdf)"],"regex_link":["GetForms"],"goto_depth":1,"jurisdiction":"MN","url":"https://www.mncourts.gov/GetForms.aspx?c={}".format(i)})
    #print(i)

In [175]:
states = [

#{"regex_form":["Download\.aspx\?id=(.*)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"DE","url":"file://../data/state_forms/_saved_html/courts.delaware.gov\\forms\\?p=1.html"}
#{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/all-forms\/"],"goto_depth":1,"jurisdiction":"OH","url":"https://www.supremecourt.ohio.gov/forms/all-forms/"}    
{"regex_form":["([^\/]*\.pdf)"],"regex_link":["\/"],"goto_depth":0,"jurisdiction":"KY","url":"file://../data/state_forms/_saved_html/kycourts.gov\\Legal-Forms\\Pages\\default.aspx.html"}
]

states

[{'regex_form': ['([^\\/]*\\.pdf)'],
  'regex_link': ['\\/'],
  'goto_depth': 0,
  'jurisdiction': 'KY',
  'url': 'file://../data/state_forms/_saved_html/kycourts.gov\\Legal-Forms\\Pages\\default.aspx.html'}]

## Run

In [5]:
%%time

visited_df = pd.DataFrame([],columns=["link"])
for state in states:
    print("======================")
    print("          %s"%state["jurisdiction"])
    print("======================")
    forms_df = pd.concat([forms_df,get_links(state["jurisdiction"],state["url"],state["regex_form"],state["regex_link"],goto_depth=state["goto_depth"],depth=0)])
    
forms_df = forms_df[~forms_df.index.duplicated(keep='first')]
display(forms_df.head())

print("\n")

if len(forms_df)>0:
    for link in forms_df.sample(n=5)["url"].values:
        print("-",link,"\n")
else:
    print("no forms found")

          MA

Checking https://www.mass.gov/guides/court-forms-by-topic
0 possible forms
Depth 0
45 links to follow
trying link...

Checking https://www.mass.gov/lists/probate-and-family-court-forms-for-wills-estates-and-trusts#accounting-forms-
43 possible forms
Depth 1
0 links to follow
43 possible forms this run

trying link...

Checking https://www.mass.gov/lists/probate-and-family-court-forms-for-actions-involving-unmarried-parents
6 possible forms
Depth 1
0 links to follow
6 possible forms this run

trying link...

Checking https://www.mass.gov/lists/probate-and-family-court-forms-for-adoption-and-name-change
3 possible forms
Depth 1
0 links to follow
3 possible forms this run

trying link...

Checking https://www.mass.gov/lists/attorney-court-forms
12 possible forms
Depth 1
0 links to follow
12 possible forms this run

trying link...

Checking https://www.mass.gov/lists/juvenile-court-forms#child-requiring-assistance-(cra)-
99 possible forms
Depth 1
0 links to follow
99 possible

67 possible forms
Depth 1
0 links to follow
67 possible forms this run

trying link...

Checking https://www.illinoiscourts.gov/documents-and-forms/employment-application
13 possible forms
Depth 1
0 links to follow
13 possible forms this run

trying link...

Checking https://www.illinoiscourts.gov/documents-and-forms/approved-forms/
14 possible forms
Depth 1
0 links to follow
14 possible forms this run

trying link...

Checking https://www.illinoiscourts.gov/documents-and-forms/uniform-mental-health-orders/
15 possible forms
Depth 1
0 links to follow
15 possible forms this run

trying link...

Checking https://www.illinoiscourts.gov/documents-and-forms/forms-probation-reimbursement-invoice-voucher/
11 possible forms
Depth 1
0 links to follow
11 possible forms this run

trying link...

Checking https://www.illinoiscourts.gov/documents-and-forms/annual-certification-of-private-insurance-coverage-form/
11 possible forms
Depth 1
0 links to follow
11 possible forms this run

trying link...


16 possible forms
Depth 1
0 links to follow
16 possible forms this run

trying link...

Checking https://www.illinoiscourts.gov/forms/approved-forms/forms-approved-forms-circuit-court/identity-theft
14 possible forms
Depth 1
0 links to follow
14 possible forms this run

trying link...

Checking https://www.illinoiscourts.gov/documents-and-forms/approved-forms/circuit-forms/identity-theft/-declaración-jurada-de-robo-de-identidad
Error Reading Page!!!
Error reading https://www.illinoiscourts.gov/documents-and-forms/approved-forms/circuit-forms/identity-theft/-declaración-jurada-de-robo-de-identidad
trying link...

Checking https://www.illinoiscourts.gov/forms/approved-forms/forms-approved-forms-circuit-court/interpreter-request
17 possible forms
Depth 1
0 links to follow
17 possible forms this run

trying link...

Checking https://www.illinoiscourts.gov/forms/approved-forms/forms-approved-forms-circuit-court/limited-scope
13 possible forms
Depth 1
0 links to follow
13 possible forms this

8 possible forms
Depth 1
0 links to follow
8 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=71
0 possible forms
Depth 1
0 links to follow
0 possible forms this run

trying link...

Checking https://www.courts.wa.gov/court_rules/?fa=court_rules.list&group=app&set=RAP
178 possible forms
Depth 1
0 links to follow
178 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=59
7 possible forms
Depth 1
0 links to follow
7 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=60
3 possible forms
Depth 1
0 links to follow
3 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.static&staticID=13
0 possible forms
Depth 1
0 links to follow
0 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=87
2 possible forms
Depth 1
0 links to 


Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=130
33 possible forms
Depth 1
0 links to follow
33 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=131
18 possible forms
Depth 1
0 links to follow
18 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=132
13 possible forms
Depth 1
0 links to follow
13 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=141
53 possible forms
Depth 1
0 links to follow
53 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=133
16 possible forms
Depth 1
0 links to follow
16 possible forms this run

trying link...

Checking https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=134
15 possible forms
Depth 1
0 links to follow
15 possible forms this run

trying link...

Checking https://www.courts.wa.go

...


Checking https://www.nccourts.gov/documents/forms/juvenile-level-2-disposition-order-delinquent
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/disposition-continuance-orderorder-to-disclose-expert-examination-records-expert-examination-order
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/comprehensive-clinical-assessment-order-to-complete-assessment-and-produce-records-comprehensive-clinical-assessment-already-completed-order-to-produce-records
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/juvenile-order-on-motion-for-review-probation-violation
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/juvenile-order-on-motion-for-review-other-th


Checking https://www.nccourts.gov/documents/forms/guardianship-capacity-questionnaire
3 possible forms
Depth 1
0 links to follow
3 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/petition-for-appointment-of-defense-counsel-for-committed-respondent-charged-with-violent-crime-for-offenses-committed-on-or-before-nov-30-2013
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/petition-for-appointment-of-defense-counsel-for-committed-respondent-charged-with-violent-crime-for-offenses-committed-on-or-after-dec-1-2013
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/petition-and-order-for-removal-of-disability-prohibiting-the-purchase-possession-or-transfer-of-a-firearm
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccour

1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/responsibilities-of-guardians-in-north-carolina
3 possible forms
Depth 1
0 links to follow
3 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/order-on-motion-for-appointment-of-interim-guardian
3 possible forms
Depth 1
0 links to follow
3 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/request-and-authorization-to-deliver-respondent
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/outpatient-commitment-order-of-assignment-or-denial-of-counsel
1 possible forms
Depth 1
0 links to follow
1 possible forms this run

trying link...

Checking https://www.nccourts.gov/documents/forms/petition-for-authorization-to-sell-motor-vehicle-under-a-lien
1 possible forms
Depth 1
0 links to follow
1 po

jurisdiction        source group title  \
ce7ec7991f0283ea319598ff05183e50           MA  www.mass.gov   NaN    \n   
13c091b90b3ee286afef69e55591d6f9           MA  www.mass.gov   NaN    \n   
c9dfc28730a9379f3cb8959d3be88386           MA  www.mass.gov   NaN    \n   
b154cdf73df83f0155f5978f748ad327           MA  www.mass.gov   NaN    \n   
88209861aa5328efab2c0082da6ed5a1           MA  www.mass.gov   NaN    \n   

                                                                                url  \
ce7ec7991f0283ea319598ff05183e50  https://www.mass.gov/doc/order-to-render-mpc-7...   
13c091b90b3ee286afef69e55591d6f9  https://www.mass.gov/doc/trust-account-mpc-859...   
c9dfc28730a9379f3cb8959d3be88386  https://www.mass.gov/doc/inventory-without-sch...   
b154cdf73df83f0155f5978f748ad327  https://www.mass.gov/doc/petition-to-modify-bo...   
88209861aa5328efab2c0082da6ed5a1  https://www.mass.gov/doc/instructions-for-comp...   

                                   filename downloaded  
ce7ec7991f0283ea319598ff05183e50  /download          0  
13c091b90b3ee286afef69e55591d6f9  /download          0  
c9dfc28730a9379f3cb8959d3be88386  /download          0  
b154cdf73df83f0155f5978f748ad327  /download          0  
88209861aa5328efab2c0082da6ed5a1  /download          0



- https://selfhelp.nvcourts.gov/images/divorce/jp-decree-nokids-pdf-fillable.pdf 

- https://www.jud.ct.gov/webforms/default.aspx?load_catg=Family#searchTable/forms/FM249.pdf 

- https://www.wicourts.gov/formdisplay/CV-404_hmn.pdf?formNumber=CV-404&formType=Form&formatId=2&language=hmn 

- https://ojd.contentdm.oclc.org/digital/custom/OJDRedirect?collection=p17027coll5&identifier=A171406.pdf 

- https://www.txcourts.gov/media/1452184/jimmy-lee-menifee.pdf 

CPU times: user 3min 26s, sys: 10.3 s, total: 3min 36s
Wall time: 1h 5min 12s


In [251]:
#with open(re.findall("file:\/\/(.*)","file://../data/state_forms/_saved_html/delaware_1.html")[0], 'r') as file:
#    page = file.read()
#page

In [6]:
state_list = ["MA","ME","UT","CA","MI","IL","MN","WA","AL","NC","CT","ID","KS","NE","VT","WI","NV","AK","CO","DE","GA","HI","VA","WY","AR","AZ","DC","FL","IA","IN","KY","LA","MD","MO","MS","MT","ND","NH","NJ","NM","NY","OH","OK","OR","PA","RI","SC","SD","TN","TX","WV"]
len(states)

262

In [7]:
grouped = forms_df.groupby(["jurisdiction"])[["url"]].count().sort_values(by=['url'], ascending=False)
print("Jurisdictions:",len(grouped),"\nForms:",len(forms_df))
print("")
for state in state_list:
    if state not in list(grouped["url"].index):
        print("Missed {}".format(state))
grouped

Jurisdictions: 46 
Forms: 30871

Missed AZ
Missed IN
Missed MO
Missed NH
Missed NM


url
jurisdiction      
CT            2707
PA            2403
WA            2084
NC            1675
CO            1593
CA            1524
TX            1199
OR            1157
DC            1129
MN            1125
MI             879
HI             867
AK             824
NE             823
DE             740
MA             718
UT             697
VT             686
OH             669
SC             620
NY             607
KY             581
ND             580
IL             578
AL             461
NV             413
FL             386
WY             385
MD             380
IA             297
RI             292
WI             281
SD             273
ID             269
ME             218
TN             138
AR             127
NJ             126
MT             116
OK              93
GA              48
VA              36
MS              25
WV              21
LA              15
KS               6

In [8]:
print(len(forms_df))
forms_df = forms_df[~forms_df.index.duplicated(keep='first')]
print(len(forms_df))

30871
30871


In [9]:
forms_df.to_csv(csv_path+"form_data.csv", index=True, encoding="utf-8")

## Download Forms

In [15]:
#for index,form in forms_df[forms_df["downloaded"]==0].sample(n=10).iterrows():
for index,form in forms_df[forms_df["downloaded"]==0].sample(frac=1).iterrows():
    print("Downloading: "+form["url"])
    try:
        status = download_pdf(form["url"],csv_path+form["jurisdiction"]+"/",index+".pdf")
        forms_df.at[index, "downloaded"] = 1
        time.sleep(random.uniform(min_wait, max_wait))
    except:
        print("ERROR downloading {}".format(form["url"]))

Downloading: https://eforms.alacourt.gov/media/gbxlpzgu/petition-for-support.pdf
Downloading: https://www.iowacourts.gov/browse/files/68d947fedd944d25bfbe3fc04641fd9b/download
Downloading: https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=137/documents/GDN ALL 007 Proof of Personal Service 2022 07.pdf
Downloading: https://www.courts.ca.gov/documents/sv720.pdf
Downloading: https://www.courts.ca.gov/documents/fl321.pdf


/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/pdfminer/pdfpage.py:140: PDFTextExtractionNotAllowedWarning: The PDF <_io.BufferedReader name='../data/state_forms/CA/5d7f9f4d9b1fe86f7361dff6abc09187.pdf'> contains a metadata field indicating that it should not allow text extraction. Ignoring this field and proceeding.
  warnings.warn(warning_msg, PDFTextExtractionNotAllowedWarning)


Downloading: https://www.dccourts.gov/sites/default/files/2019-07/STANDBY%20GUARDIAN%20DESIGNATION%20FORM.pdf
Downloading: https://supremecourt.nebraska.gov/sites/default/files/DC-6-5-25.pdf
Downloading: https://www.courts.ca.gov/documents/ej158.pdf
Downloading: https://www.courts.state.co.us/Forms/renderWord.cfm?Form=292
Downloading: https://www.pacourts.us/Storage/media/pdfs/20210515/220322-file-3664.pdf
Downloading: https://kycourts.gov/Legal-Forms/Legal Forms/FC-1.pdf
Downloading: https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=106/documents/XR 201 Petition for an Extreme Risk Protection Order - Respondent Under 18 Years_2022 07.pdf
Downloading: https://www.flcourts.gov/content/download/685843/file_pdf/911c.pdf
Downloading: https://www.courts.wa.gov/forms/?fa=forms.contribute&formID=25/documents/FL All Family 185 Notice of Hearing.pdf
Downloading: https://www.courts.state.wy.us/wp-content/uploads/2017/05/civpro_2012082300.pdf
Downloading: https://www.jud.ct.gov/webforms

/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/pdfminer/pdfpage.py:140: PDFTextExtractionNotAllowedWarning: The PDF <_io.BufferedReader name='../data/state_forms/CA/42ac16009d00491ea5051b211bb12690.pdf'> contains a metadata field indicating that it should not allow text extraction. Ignoring this field and proceeding.
  warnings.warn(warning_msg, PDFTextExtractionNotAllowedWarning)


Downloading: https://www.courts.ca.gov/documents/civ100.pdf
Downloading: https://www.mncourts.gov/mncourtsgov/media/CourtForms/CSX1702.pdf?ext=.pdf
Downloading: https://www.nycourts.gov/legacypdfs/courts/10jd/suffolk/dist/pdf/OSC_pg1.pdf
Downloading: https://www.dccourts.gov/sites/default/files/2018-01/Request%20to%20File%20Foreign%20Judgment_AMH.pdf
Downloading: https://www.pacourts.us/Storage/media/pdfs/20210510/122641-file-10848.pdf
Downloading: https://www.nycourts.gov/LegacyPDFS/forms/familycourt/pdfs/SC-3.pdf
Downloading: https://selfhelp.nvcourts.gov/images/guardianship/gship-consent-misc-pdf.pdf
Downloading: https://www.courts.state.wy.us/wp-content/uploads/2017/04/DWCP15.pdf
Downloading: https://www.courts.state.md.us/sites/default/files/court-forms/ccdr063.pdf
Downloading: https://www.courts.ca.gov/documents/jv206.pdf


...

Downloading: https://ujs.sd.gov/uploads/forms/evictions/UJS109_INSTRUCTIONS_FOR_EVICTION_ACTIONS.pdf
Downloading: https://www.jud.ct.gov/webforms/../directory/directory/smallclaims.htm/../../../directory/juddir.pdf#page=144
Downloading: https://www.txcourts.gov/media/1454849/edmund-heimlich.pdf
Downloading: https://www.nycourts.gov/courts/nyc/smallclaims/forms.shtml/../civil/forms/CIV-SC-63.pdf
Downloading: https://www.courts.state.co.us/Forms/renderForm1.cfm?Form=346
Downloading: https://www.ndcourts.gov/Media/Default/legal-resources/legal-self-help/juvenile-action/Motion-Appear-REM-Juv-Ct.pdf
Downloading: https://www.courts.state.co.us/Forms/renderForm1.cfm?Form=884
Downloading: https://www.nycourts.gov/courts/AD2/forms/noticeofmotion-NEW.pdf
Downloading: https://www.jud.ct.gov/webforms/default.aspx?load_catg=Juvenile#searchTable/forms/JM098.pdf
Downloading: https://www.courts.ca.gov/documents/jv464info.pdf


/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/pdfminer/pdfpage.py:140: PDFTextExtractionNotAllowedWarning: The PDF <_io.BufferedReader name='../data/state_forms/CA/5f0ca7fd7a5ad6e35ee1e0f97fed0aa5.pdf'> contains a metadata field indicating that it should not allow text extraction. Ignoring this field and proceeding.
  warnings.warn(warning_msg, PDFTextExtractionNotAllowedWarning)


Downloading: https://www.dccourts.gov/sites/default/files/2018-02/Statement%20of%20criminal%20history_Case%20Initiation%20INT_SPA.pdf
Downloading: https://supremecourt.nebraska.gov/sites/default/files/Ch6Art14App2H.pdf
Downloading: https://www.nccourts.gov/assets/documents/forms/cv313-vi.pdf?VersionId=P7_XsTz8NnUuEu.8KSsLvy.T.uLFxOA_
Downloading: https://www.jud.ct.gov/webforms/default.aspx?load_catg=Family#searchTable/forms/XFA/FM125_XFA.pdf
Downloading: https://ojd.contentdm.oclc.org/digital/custom/OJDRedirect?collection=p17027coll5&identifier=A173018.pdf
Downloading: https://www.courts.ri.gov/PublicResources/forms/Superior Court Forms/Pro Hac Vice - Attorney Certification for Admission Pro Hac Vice.pdf
Downloading: https://www.jud.ct.gov/webforms/../polski.htm/Publications/VS017P.pdf
Downloading: https://www.courts.state.co.us/Forms/renderWord.cfm?Form=247
Downloading: https://www.ndcourts.gov/Media/Default/Legal%20Resources/Legal%20Self%20Help/Name%20Change/Order-name-change-child.

/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/pdfminer/pdfpage.py:140: PDFTextExtractionNotAllowedWarning: The PDF <_io.BufferedReader name='../data/state_forms/CA/ca93f73a9d4984d19d305c595331b344.pdf'> contains a metadata field indicating that it should not allow text extraction. Ignoring this field and proceeding.
  warnings.warn(warning_msg, PDFTextExtractionNotAllowedWarning)


Downloading: https://www.courts.state.co.us/Forms/renderWord.cfm?Form=220
Downloading: https://www.courts.ri.gov/PublicResources/forms/Workers Compensation Court Forms/Request for Transcript.pdf
Downloading: https://www.courts.ca.gov/documents/cr112.pdf
Downloading: https://www.arcourts.gov/sites/default/files/formatted-files/2017_CV_disp_instructions.pdf
Downloading: https://www.courts.ri.gov/PublicResources/forms/Superior Court Forms/Writ of Replevin.pdf
Downloading: https://public.courts.alaska.gov/web/forms/docs/tr-425.pdf
Downloading: https://www.pacourts.us/Storage/media/pdfs/20220103/214537-44-mm-2020-lancco.6.pdf
Downloading: https://www.courts.state.co.us/Forms/renderForm1.cfm?Form=1055
Downloading: https://www.courts.wa.gov/forms/?fa=forms.static&staticID=14/documents/XR 125  Order Trans Case to Super Ct set Hrg_2022_07.pdf
Downloading: https://www.mncourts.gov/mncourtsgov/media/CourtForms/FOR102.pdf?ext=.pdf


In [16]:
print("Downloaded:",len(forms_df[forms_df["downloaded"]==1]))
print("Pending:",len(forms_df[forms_df["downloaded"]==0]))
print("All Entries:",len(forms_df))
forms_df#.sample(n=5)

Downloaded: 30871
Pending: 0
All Entries: 30871


jurisdiction            source group  \
ce7ec7991f0283ea319598ff05183e50           MA      www.mass.gov   NaN   
13c091b90b3ee286afef69e55591d6f9           MA      www.mass.gov   NaN   
c9dfc28730a9379f3cb8959d3be88386           MA      www.mass.gov   NaN   
b154cdf73df83f0155f5978f748ad327           MA      www.mass.gov   NaN   
88209861aa5328efab2c0082da6ed5a1           MA      www.mass.gov   NaN   
...                                       ...               ...   ...   
ec8c049e6479b51764fc996b75574b5e           NC  www.nccourts.gov   NaN   
75034ca65ad5657838264da8fbeabc94           NC  www.nccourts.gov   NaN   
c75fde2921d9e36b71ac723582dee4d7           NC  www.nccourts.gov   NaN   
1efbb93bcedfbbb86c6eb9dbbab89f83           NC  www.nccourts.gov   NaN   
24424ecd1a9bccf447055f4e4725c13f           NC  www.nccourts.gov   NaN   

                                                                              title  \
ce7ec7991f0283ea319598ff05183e50                                                 \n   
13c091b90b3ee286afef69e55591d6f9                                                 \n   
c9dfc28730a9379f3cb8959d3be88386                                                 \n   
b154cdf73df83f0155f5978f748ad327                                                 \n   
88209861aa5328efab2c0082da6ed5a1                                                 \n   
...                                                                             ...   
ec8c049e6479b51764fc996b75574b5e   \n      Order Voluntary Admission Of Minor\n       
75034ca65ad5657838264da8fbeabc94  \n      Orden Ingreso Voluntario De Un Menor\n...   
c75fde2921d9e36b71ac723582dee4d7  \n      Án Lệnh Cho Trẻ Vị Thành Niên Nhập Việ...   
1efbb93bcedfbbb86c6eb9dbbab89f83  \n      Release Of Physical And Mental Health,...   
24424ecd1a9bccf447055f4e4725c13f                \n      Order to File Account\n       

                                                                                url  \
ce7ec7991f0283ea319598ff05183e50  https://www.mass.gov/doc/order-to-render-mpc-7...   
13c091b90b3ee286afef69e55591d6f9  https://www.mass.gov/doc/trust-account-mpc-859...   
c9dfc28730a9379f3cb8959d3be88386  https://www.mass.gov/doc/inventory-without-sch...   
b154cdf73df83f0155f5978f748ad327  https://www.mass.gov/doc/petition-to-modify-bo...   
88209861aa5328efab2c0082da6ed5a1  https://www.mass.gov/doc/instructions-for-comp...   
...                                                                             ...   
ec8c049e6479b51764fc996b75574b5e  https://www.nccourts.gov/assets/documents/form...   
75034ca65ad5657838264da8fbeabc94  https://www.nccourts.gov/assets/documents/form...   
c75fde2921d9e36b71ac723582dee4d7  https://www.nccourts.gov/assets/documents/form...   
1efbb93bcedfbbb86c6eb9dbbab89f83  https://www.nccourts.gov/assets/documents/form...   
24424ecd1a9bccf447055f4e4725c13f  https://www.nccourts.gov/assets/documents/form...   

                                                  filename downloaded  
ce7ec7991f0283ea319598ff05183e50                 /download          1  
13c091b90b3ee286afef69e55591d6f9                 /download          1  
c9dfc28730a9379f3cb8959d3be88386                 /download          1  
b154cdf73df83f0155f5978f748ad327                 /download          1  
88209861aa5328efab2c0082da6ed5a1                 /download          1  
...                                                    ...        ...  
ec8c049e6479b51764fc996b75574b5e                 sp913.pdf          1  
75034ca65ad5657838264da8fbeabc94   SP-913_rev10-19_SPA.pdf          1  
c75fde2921d9e36b71ac723582dee4d7  SP-913M_rev10-19_VIE.pdf          1  
1efbb93bcedfbbb86c6eb9dbbab89f83                 sp914.pdf          1  
24424ecd1a9bccf447055f4e4725c13f              sp915-en.pdf          1  

[30871 rows x 7 columns]

In [17]:
forms_df.to_csv(csv_path+"form_data.csv", index=True, encoding="utf-8")

In [6]:
import psutil
# gives a single float value
psutil.cpu_percent()

12.0

False

In [5]:
# gives an object with many fields
psutil.virtual_memory()

svmem(total=34359738368, available=16927551488, percent=50.7, used=15526649856, free=4679499776, active=11946471424, inactive=12056522752, wired=3580178432)

In [4]:
# you can convert that object to a dictionary 
dict(psutil.virtual_memory()._asdict())

{'total': 34359738368,
 'available': 16771153920,
 'percent': 51.2,
 'used': 15683497984,
 'free': 4669493248,
 'active': 12104220672,
 'inactive': 11918835712,
 'wired': 3579277312}

In [3]:
# you can have the percentage of used RAM
psutil.virtual_memory().percent

51.3

In [2]:
# you can calculate percentage of available memory
psutil.virtual_memory().available * 100 / psutil.virtual_memory().total

48.716139793395996

In [11]:
import psutil, time
#from IPython.display import display, Javascript

def governor(wait=0):
    wait_tick = 10
    cpu = psutil.cpu_percent()
    mem = psutil.virtual_memory().percent
    print("\n=======================================")
    print(" Usage: CPU {}% & Memory {}%".format(cpu,mem))
    if (wait<0):
        print("   Full speed ahead!")
        
    elif (wait>(wait_tick*8)):    
        print("    Shut it down!!!")
        #display(Javascript('IPython.notebook.save_checkpoint();'))
        time.sleep(5)
        quit()
    
    elif (cpu > 33) | (mem > 66.66):
        print("    Slowing down...")
        time.sleep(wait)
        governor(wait+wait_tick)
    
    print("=======================================\n")
    

In [12]:
governor()


 Usage: CPU 12.6% & Memory 54.3%



In [57]:
x_1 = pd.read_json("/Users/davidcolarusso/Documents/GitHub/FormExplorer/data/state_forms/all_together_now/1_8000/stats.json", orient='index')
x_2 = pd.read_json("/Users/davidcolarusso/Documents/GitHub/FormExplorer/data/state_forms/all_together_now/8001_16000/stats.json", orient='index')
x_3 = pd.read_json("/Users/davidcolarusso/Documents/GitHub/FormExplorer/data/state_forms/all_together_now/16001_x/stats.json", orient='index')
x = pd.concat([x_1,x_2,x_3])
print(len(x))
x

24061


title  \
9fffe321a9fbafdb7964293e8c88e265.pdf                                 Writ of Possession   
9fffc9d14d491929bae5c6cecc03e7c7.pdf                                               hrcc   
9ffd35f8778e21212dd0f319ebb497d2.pdf  Instructions For Florida Supreme Court Approve...   
9ffba05824a302bc69c7fded6244af49.pdf              GAL - Fee Waiver Application (Family)   
9ff5c8ab7729bc4343ab717c29dba495.pdf                                  STATE OF NEBRASKA   
...                                                                                 ...   
a12264898b761f4ecdac8977db1116c0.pdf                       INSTRUCTIONS FOR FILLING OUT   
a078923719fb98f59f9a95de2ad6bfb0.pdf  Home Detention Screening Criteria (for Home De...   
a074881877409c04b648a9fa2aee6361.pdf  Microsoft Word - D4F99D126C08CAF6FD5BB80FD7CFF...   
a025934264e01073990c9c9707dea193.pdf                                         (Untitled)   
a0201576605f0db775252d8d88fc4d1d.pdf  CIV-853 Order on Motion for Judgment on the Pl...   

                                     suggested title description  category  \
9fffe321a9fbafdb7964293e8c88e265.pdf                                   NaN   
9fffc9d14d491929bae5c6cecc03e7c7.pdf                                   NaN   
9ffd35f8778e21212dd0f319ebb497d2.pdf                                   NaN   
9ffba05824a302bc69c7fded6244af49.pdf                                   NaN   
9ff5c8ab7729bc4343ab717c29dba495.pdf                                   NaN   
...                                              ...         ...       ...   
a12264898b761f4ecdac8977db1116c0.pdf                                   NaN   
a078923719fb98f59f9a95de2ad6bfb0.pdf                                   NaN   
a074881877409c04b648a9fa2aee6361.pdf                                   NaN   
a025934264e01073990c9c9707dea193.pdf                                   NaN   
a0201576605f0db775252d8d88fc4d1d.pdf                                   NaN   

                                      pages  reading grade level  \
9fffe321a9fbafdb7964293e8c88e265.pdf      2                   13   
9fffc9d14d491929bae5c6cecc03e7c7.pdf     20                   13   
9ffd35f8778e21212dd0f319ebb497d2.pdf      9                   20   
9ffba05824a302bc69c7fded6244af49.pdf      3                   10   
9ff5c8ab7729bc4343ab717c29dba495.pdf      2                    8   
...                                     ...                  ...   
a12264898b761f4ecdac8977db1116c0.pdf      2                    7   
a078923719fb98f59f9a95de2ad6bfb0.pdf      4                   10   
a074881877409c04b648a9fa2aee6361.pdf      3                   13   
a025934264e01073990c9c9707dea193.pdf      1                   11   
a0201576605f0db775252d8d88fc4d1d.pdf      1                    8   

                                     time to answer list  avg fields per page  \
9fffe321a9fbafdb7964293e8c88e265.pdf     [5.3, 1.9]   []             5.500000   
9fffc9d14d491929bae5c6cecc03e7c7.pdf  [120.0, 12.0]   []             4.600000   
9ffd35f8778e21212dd0f319ebb497d2.pdf    [83.0, 9.7]   []             7.888889   
9ffba05824a302bc69c7fded6244af49.pdf    [24.0, 4.4]   []            12.666667   
9ff5c8ab7729bc4343ab717c29dba495.pdf     [5.2, 2.4]   []             2.500000   
...                                             ...  ...                  ...   
a12264898b761f4ecdac8977db1116c0.pdf    [22.0, 4.3]   []            18.000000   
a078923719fb98f59f9a95de2ad6bfb0.pdf    [16.0, 3.2]   []             8.250000   
a074881877409c04b648a9fa2aee6361.pdf     [2.0, 1.1]   []             1.333333   
a025934264e01073990c9c9707dea193.pdf    [46.0, 7.6]   []            25.000000   
a0201576605f0db775252d8d88fc4d1d.pdf    [28.0, 5.9]   []            15.000000   

                                                                                 fields  \
9fffe321a9fbafdb7964293e8c88e265.pdf  [clerk_district_court_state, duly_authorized_l...   
9fffc9d14d491929bae5c6cecc03e7c7.pdf  [cas_e_number, cite_authorizing_statutes, 

In [46]:
x.sample(100)["title"]

e08ee0429621e2e2f9a061f703a54874.pdf                                STATE OF SOUTH DAKOTA
8e6235dbeaf4a2d60c3c487b9dc1291d.pdf                                           (Untitled)
611aa1975c777ce076e4c9fd5c02d7e6.pdf    STATE OF RHODE ISLAND                         ...
7e0b3a06771b16549621acdde76b1637.pdf                                           (Untitled)
4cf510c5fbdf5244373d7dd875e58df6.pdf                   Affidavit of Out-of-State Attorney
                                                              ...                        
f0bef4b0aefe22716be2191b0751040a.pdf                          Affidavit of Mailing Notice
a644efc3d493fdae2d230d18b90dc1d1.pdf                                 Moving Party’s name 
6ea362c04e1b4217019b764417e43a04.pdf      FL-327 ORDER APPOINTING CHILD CUSTODY EVALUATOR
f1b7d013ff4de27857ee090182db4548.pdf    Debtor’s Motion to Declare the Judgment Satisfied
61679e836634813563bf4aa2d8149f7b.pdf                     Rules for Filing Court Pleadings
Name: titl

In [49]:
x[x["title"]=="(Untitled)"]

title suggested title description  \
9fe25a41e4adb457620311fec4535552.pdf  (Untitled)                               
9fe23bcff7e7e5a5c5f4a40a34614b08.pdf  (Untitled)                               
9fdf23c877e0f2ba516e16fc4afcb98a.pdf  (Untitled)                               
9fde56f46b265d2f2e9389f9f1cd2e9c.pdf  (Untitled)                               
9fd711f53e91c80c8977a8e386b2439b.pdf  (Untitled)                               
...                                          ...             ...         ...   
d3f052cd5d0671241dce6cddac258604.pdf  (Untitled)                               
d3ec08b308ff88ca9375edbc23bb3ea3.pdf  (Untitled)                               
d3dc1172fdf6b35763e0a1559d839523.pdf  (Untitled)                               
d3c9eae3733acc48504d51deb9fe300f.pdf  (Untitled)                               
d3c28e399592d1f3e2314da0aa917231.pdf  (Untitled)                               

                                      category  pages  reading grade level  \
9fe25a41e4adb457620311fec4535552.pdf       NaN      2                   13   
9fe23bcff7e7e5a5c5f4a40a34614b08.pdf       NaN      1                   13   
9fdf23c877e0f2ba516e16fc4afcb98a.pdf       NaN      1                    8   
9fde56f46b265d2f2e9389f9f1cd2e9c.pdf       NaN      2                   11   
9fd711f53e91c80c8977a8e386b2439b.pdf       NaN     10                   10   
...                                        ...    ...                  ...   
d3f052cd5d0671241dce6cddac258604.pdf       NaN      1                   15   
d3ec08b308ff88ca9375edbc23bb3ea3.pdf       NaN      2                    9   
d3dc1172fdf6b35763e0a1559d839523.pdf       NaN      1                    9   
d3c9eae3733acc48504d51deb9fe300f.pdf       NaN      2                    8   
d3c28e399592d1f3e2314da0aa917231.pdf       NaN      2                   12   

                                                 time to answer list  \
9fe25a41e4adb457620311fec4535552.pdf               [0.49, 0.56]   []   
9fe23bcff7e7e5a5c5f4a40a34614b08.pdf                [10.0, 3.3]   []   
9fdf23c877e0f2ba516e16fc4afcb98a.pdf                [31.0, 5.9]   []   
9fde56f46b265d2f2e9389f9f1cd2e9c.pdf              [120.0, 12.0]   []   
9fd711f53e91c80c8977a8e386b2439b.pdf  [4.4, 1.7000000000000002]   []   
...                                                         ...  ...   
d3f052cd5d0671241dce6cddac258604.pdf                   [-1, -1]   []   
d3ec08b308ff88ca9375edbc23bb3ea3.pdf                [73.0, 9.4]   []   
d3dc1172fdf6b35763e0a1559d839523.pdf                [26.0, 5.6]   []   
d3c9eae3733acc48504d51deb9fe300f.pdf                [45.0, 7.2]   []   
d3c28e399592d1f3e2314da0aa917231.pdf              [200.0, 16.0]   []   

                                      avg fields per page  \
9fe25a41e4adb457620311fec4535552.pdf                  0.5   
9fe23bcff7e7e5a5c5f4a40a34614b08.pdf                 11.0   
9fdf23c877e0f2ba516e16fc4afcb98a.pdf                 27.0   
9fde56f46b265d2f2e9389f9f1cd2e9c.pdf                 27.5   
9fd711f53e91c80c8977a8e386b2439b.pdf                  0.9   
...                                                   ...   
d3f052cd5d0671241dce6cddac258604.pdf                  0.0   
d3ec08b308ff88ca9375edbc23bb3ea3.pdf                 24.0   
d3dc1172fdf6b35763e0a1559d839523.pdf                 17.0   
d3c9eae3733acc48504d51deb9fe300f.pdf                 18.0   
d3c28e399592d1f3e2314da0aa917231.pdf                 38.0   

                                                                                 fields  \
9fe25a41e4adb457620311fec4535552.pdf                                         [dropdown]   
9fe23bcff7e7e5a5c5f4a40a34614b08.pdf  [juzgado_distrito_familia, krs, con_si_es_da_d...   
9fdf23c877e0f2ba516e16fc4afcb98a.pdf  [plaintiff, defendant, civil_action_file_numbe...   
9fde56f46b265d2f2e9389f9f1cd2e9c.pdf  [ncjoin, *docket_number, county_name, juvenile...   
9fd711f53e91c80c8977a8e386b2439b.pdf  [person, page_field__1, debtor_exams_remote, m...   
.

In [35]:
x.columns

Index(['title', 'suggested title', 'description', 'category', 'pages',
       'reading grade level', 'time to answer', 'list', 'avg fields per page',
       'fields', 'fields_conf', 'fields_old', 'number of sentences',
       'sentences per page', 'number of passive voice sentences',
       'passive sentences', 'number of all caps words', 'citations',
       'total fields', 'slotin percent', 'gathered percent', 'created percent',
       'third party percent', 'passive voice percent', 'citations per field',
       'citation count', 'all caps percent', 'difficult words',
       'difficult word count', 'difficult word percent',
       'calculation required'],
      dtype='object')

In [59]:
x.sample(1000) #.to_csv(csv_path+"form_scratch.csv", index=True, encoding="utf-8")

In [61]:
for index,row in x.iterrows():
    print(index)

9fffe321a9fbafdb7964293e8c88e265.pdf
9fffc9d14d491929bae5c6cecc03e7c7.pdf
9ffd35f8778e21212dd0f319ebb497d2.pdf
9ffba05824a302bc69c7fded6244af49.pdf
9ff5c8ab7729bc4343ab717c29dba495.pdf
9fe94d3345a6aaa2162938f87d21425c.pdf
9fe32411da37d9b854d5212da788d180.pdf
9fe25a41e4adb457620311fec4535552.pdf
9fe23bcff7e7e5a5c5f4a40a34614b08.pdf
9fdf23c877e0f2ba516e16fc4afcb98a.pdf
9fde56f46b265d2f2e9389f9f1cd2e9c.pdf
9fd874fe746448a33f72ba7e0095068f.pdf
9fd711f53e91c80c8977a8e386b2439b.pdf
9fd51c4b080be4dbd2bc43c2cab3c0ed.pdf
9fd4bdcc64bd354bb0a186d5d4d86e99.pdf
9fd1ba95a1947dc289b60287be928ed2.pdf
9fcde670807e3a1c7248fd852c900bc3.pdf
9fca821553f4d8c72bf87bb14b38ddb2.pdf
9fc4d37abebffac0ac0b9617b7825755.pdf
9fbf88b42da93d1f7c6702cdb8e0be7a.pdf
9fbb5f883509cfdccbe9274f07fb8d9e.pdf
9fb22451687e10b06dc6a20aba84e910.pdf
9fb063fced01d2d5705fa113a71fc6e9.pdf
9fad0e2f5433e7485cdb6a0bd6e1f903.pdf
9fa46e71cfe050adbfd6948c9f6b1286.pdf
9fa40f194cc9f0610d3f6c82d1d09afc.pdf
9fa3d871437b982420e2cd1b208eb211.pdf
9

7caf8ad70ee7b1c02eda89c69ca76acd.pdf
7cacdb18a8c8c6e04369a53c490aa395.pdf
7ca2c66ddc038c43315a2c4a91170254.pdf
7c9fe581e42908bcce7c744d5b37f653.pdf
7c9c83bdf40210effc5702daa7f0326d.pdf
7c9551982a86e2e5ea000ec145b59a92.pdf
7c933b3b362920dfcd12f67f31fbeed1.pdf
7c90891c9ea75de413b269d64eaff1c8.pdf
7c8f73818a3a1ac502f83f826a7e0894.pdf
7c8c8b0e69fcd870654c4a0369d0a7a2.pdf
7c8c31422eef2ab4bb94e9e339036edd.pdf
7c8a88d5fd7f729a3f77c84e30ee5084.pdf
7c8996ed7107100589fe1f8da23e403d.pdf
7c881734d8259859730533ed45a761c2.pdf
7c87f1cd6e8a293e6bb8163419477121.pdf
7c815c942e3692bd85aa3ec39d669550.pdf
7c7d575bf41f51cce4f717da5a188515.pdf
7c7850826056e4b5bc93cba7b4064a19.pdf
7c774ba4e0bcba4f500da1673f0eedb0.pdf
7c76d3fe74c413db02908dca00d48de0.pdf
7c7152db296c4e4de13986cae50df600.pdf
7c6ee97b72d7762908f0a9923d8d424c.pdf
7c6c17ba4c6cca8940dcf475f012e8d5.pdf
7c640d72afec3618eb269ccd767e9206.pdf
7c60aec153066c31250c9b242f94d982.pdf
7c5ff01e23a2519f21edd3d7c665c49c.pdf
7c5c48e2eff3428d85d44807289e671a.pdf
7

5c31452bbaeb2a69746d5178d45086ea.pdf
5c2f749955dc06f7dfd271e989220b84.pdf
5c28d9bc59993c0d6e6ae5c34d617a47.pdf
5c28233c43f1ae69b3db356d49ffdd8d.pdf
5c24861824885e93aeefa6366c145242.pdf
5c2117481873926f7eb4efd7cd7be786.pdf
5c1f3676dbd077e3f7c0f718542b6c00.pdf
5c1eb5a52cc1636edfb0c20136c6afb9.pdf
5c1b4b11fdf33042da118fd593ec2331.pdf
5c1a95015376af294ee03ee7cf1cc494.pdf
5c105932a293fd8ec0ef4c1beab14d5b.pdf
5c0fff25ea221b0e49a647924e2a4d3d.pdf
5c0bc0a813b0538f3b9b45ab7cdee6a9.pdf
5c0948a14b69590a9cfd0c6fbb9d4039.pdf
5c08a30e328c08e50df3949d8e7c2f3a.pdf
5c067965326fec9c3a8e2bc0c1944521.pdf
5c064722ea23831e5cd70d3841afb77b.pdf
5c04529b04a952423d67074a37922a4d.pdf
5bff010c50ddaa1f3bc406c9bd3bd97c.pdf
5bfee6995773670cb0db6eae66dc3fc8.pdf
5bfecf64e41799adf0c3e15b24118d90.pdf
5bfc39677ebf29bd3579f67276a9a3f4.pdf
5bfb02d911722b5f9931eb8a4b0655a2.pdf
5bf2dd70c6942bc659b6845d4389c397.pdf
5befe6713687b9932e69bd78e1b4df3f.pdf
5bed2402303e764a221eead94e2378b0.pdf
5beb3ec4a33e08f49f83908813e68976.pdf
5

47ac77e07694f27e3f93633eaa96a43e.pdf
47a8a04787b4ace8a97389b9bf020b99.pdf
47a86fd656121f94b7202d54a8f22853.pdf
47a198010ca4c0fc445e91eae063f72b.pdf
47a149364191a432b52a44d696c1db6b.pdf
47a024da41177f394a3050f5376809ec.pdf
46fb419e4a44aa1f8897f1334250177f.pdf
46f908eb7b71ca1ab75397896dbb6ad0.pdf
46f7edd58ded249f88a6ad6f5fd175b2.pdf
46f6c04579014e5c274f1c3be452d214.pdf
46f44b4ae75e99790f279521a75d864b.pdf
46f43e2934310862f3700da83af9e2e8.pdf
46f0825d08df762bd435bd957f90c082.pdf
46ec265cf7a6eadd8884fdbbe9e8cb4a.pdf
46ebbc48ddd7c9d54e74ac72491b28ae.pdf
46ea2bb7a3dac3ad8993b7a01ab105c2.pdf
46e518f044a923b8742a3cd655537a2d.pdf
46e4d61cf2a02c278546e3aa75665e06.pdf
46dd8d7c740fff1b827a37bcb4190638.pdf
46d840e963e3c83e005d03d490d37bea.pdf
46d6844a56599d982b5120b9bcf74813.pdf
46d530afe30aa5a32dc6408665f2cd0a.pdf
46d4e2466abf6df0fda9d7744cfa9d54.pdf
46d4ce6d435fd1e7752e56f61805a47d.pdf
46d2bbcba1265e28ec776701ecf86bb1.pdf
46cebe33de6823e6d3516d6c0f7fb4ca.pdf
46cc1f757fb598922574f1f3f38c8b63.pdf
4

2dadf34621714dbb7bc3a3ae7c405836.pdf
2dad64aa48cb40082d11caf818b14226.pdf
2dab316fbdec33e70d4e7dc6b2d2e187.pdf
2da9371c6e9401c433690a2a9fba7637.pdf
2da8b3456a097ed1959e4c1a40a98060.pdf
2da52a4cd99e19ff39a61972f3304e6a.pdf
2da1a1649151abf613d3260de70f2fd4.pdf
2d9b5eb44a1e39ebff998d15b74e2b49.pdf
2d98c40b8fa51f72714caed522ec4fd5.pdf
2d970c69f4d4526beee79ee3ad2deba5.pdf
2d95c22b3f69cd00499854d9b562b7cb.pdf
2d94bf5b604b326214889d5a3700ab7a.pdf
2d8df38b1c7c2007b3c59b9e405676ca.pdf
2d86ae970193d9a052e2ca354189e1d0.pdf
2d8670a21095d264d906c9bd3ef18431.pdf
2d866332fe6013d13c2213e4e61b6b21.pdf
2d83f8f3045992bfa13e271f8988ec26.pdf
2d83f10d13b8e22e51f55a22720be93f.pdf
2d83a925daf83b3eb0a5e99a1e4a0df8.pdf
2d77bb97a02c918efa7342c394319271.pdf
2d76e7abbc85b754829d896cbac6b86f.pdf
2d72f54b48f978e553964b722dee7a74.pdf
2d72ef4fed473886ecbf54207688bb00.pdf
2d6df2996326f9a41ab5290c5c419045.pdf
2d64e73eba5cbe97801387cfa895e5c0.pdf
2d62acc7a45b72cf6640d2e919c8093d.pdf
2d5b5edf57dbcc3798234915fd1fbf50.pdf
2

...

e76babdb676391d7b53262d06f599bef.pdf
e76b212b9a7efd73a4e6d4e65b717cb2.pdf
e768683d2897d3959bc5a4b3c26fbb44.pdf
e761f9db446fbedb96198d9fa244b498.pdf
e7611977eb3c1711ce3337046d25a8e0.pdf
e75ea8915f96612745f92f396649a273.pdf
e754a5b35477c5ae92b0e0b76040c0dd.pdf
e74f42b2bd82d7b5dc3a064fb2843aed.pdf
e74e9986541133b57079b14eb4b8e308.pdf
e74b77e4b60c3e434dff0e1121df78f7.pdf
e74879f1d7cd2f08e00658b72e4ab48e.pdf
e7486db63b5934acd66afa6e0615cb18.pdf
e7479842d629c36dd6bb8e752e8762c9.pdf
e745aae812b24469b554fd2c40f9b1a2.pdf
e743bdfea2ccd0c8c5419711c5a29f80.pdf
e743b5677d92cc17a4a740ca89621f01.pdf
e7417db3aea131b9c9d4e6a4835db275.pdf
e7410eb5bf9e009dd5422e2f96acdb64.pdf
e73cadc58a96c0ede87d47062e9463a4.pdf
e73a61b2824b8df3fafe3cc5872a8ff0.pdf
e73a3d878092c3b3f55a5681a1a1d4a0.pdf
e7376cdd7a016705b13a62e9fed59902.pdf
e736b0f49c4f7c58ffb68b3151c7f68c.pdf
e734509a1ddb9ab3b3176e4afdb2c670.pdf
e733d4cc6051b864f5a7c3038a2050c0.pdf
e72c0214f6d054259eae1f1d96bb4d82.pdf
e727073372e00efa556d9e666f6271e9.pdf
e

dae28e42622007194a5bc16460317688.pdf
dadfa2199fdd8d72fe53839bbf56219d.pdf
dadeffe29ff92993e078df3398a4ce4f.pdf
dadbc7a61afdc21a069d71f2402f028c.pdf
dada517cdb0065e0b68669538791e401.pdf
dad963d62d47cfb4cca1185964a10ee4.pdf
dad7c8671ae10b2513c03592c44d0fd6.pdf
dad6469d12854dc10819cb59b5ea4f44.pdf
dad4e92a18b42981a8131e0005f27e7d.pdf
dad4b77ce4eb2d5c8e54d80178fb15b0.pdf
dad40c510a14b4629e2a95103189d19f.pdf
dacfee9f25f812799699052c160a91d9.pdf
dac9ae3ae3eabb59e3d20a3a4d3c22b1.pdf
dac966738ed09e736b0a0341c631938c.pdf
dac85cc47becee428256d59cb6b0b289.pdf
dac66455edad9c662c1dfd79fc26ab30.pdf
dac3da04c901a4234897ed51a0ad0dd4.pdf
dac0e0373e29533ea82274858424527a.pdf
dabed68bef755272bcefad4b407c9297.pdf
dabb6ae0b2d76c33fa5fcd94e1a7afe0.pdf
dabb3c4b85df7d3bdffaf82b8e7dbfef.pdf
dab6043be58c091c942ffcfd916ff158.pdf
dab5250a1be30101e8f101578d665951.pdf
daab952f9a29e74f48ab90bec0af8a3b.pdf
daab4257ab7fd40d27a390d118b4e416.pdf
daaa929771daee80075df6ccf939ca0d.pdf
daa87a74d7d66c9e7c71acece03c46aa.pdf
d

cc97d1e99128e67e11aac31f707619ab.pdf
cc9338862a6d0362b238bdfb3d9272f7.pdf
cc92ba9359cdb222785b2c668b84b9b1.pdf
cc89a997afbd907ae6449fcdafbae2d7.pdf
cc88c86ece3272dcdcd9a6be5b873191.pdf
cc88334d73574906e24b712e523ecbd4.pdf
cc873e2107bf37f8db61eb611d2a2cee.pdf
cc81f69fa5bf689bb3893c676c84bcbc.pdf
cc81b3002de2c318b541878b00999478.pdf
cc7ce79ea66ecd7d33b2202f029d87b2.pdf
cc7b0cfb66a491e443d3209e4d945bc7.pdf
cc7a89fad5957215721a1e5b24de9a2d.pdf
cc6fcf35a9509529bac5b47596aecbf2.pdf
cc6cc5c725f48127cb9ab2f658ddac2a.pdf
cc6a775d7a11768bd2a713d9a7139b3d.pdf
cc68d7a726fd2c4dfc072fb72fc54c3d.pdf
cc660b07133ab66a5ef7e55cf52a8385.pdf
cc63ed445cb224ddb48dfd8ecc745b26.pdf
cc637c70c36f934697191509ddb51bbf.pdf
cc61d490298a3608390173ccc2dfd878.pdf
cc603aae33d7d4cef326666140255bea.pdf
cc600b342f9a256c4ded6787d0b1a733.pdf
cc5c2c5fc201abd8ca4a69e732f0211c.pdf
cc545ce1e3394d848802d6de62a21d73.pdf
cc5333de333af7487a0fdf05f2025fec.pdf
cc4facab72b959fa4a80077651561334.pdf
cc45c99bd24af554b935ec1cf34f355e.pdf
c

c05ea1e0993c2cb25c2f727b71f08c1d.pdf
c0573a6221dafac8a7153d3d0944b140.pdf
c052671865fb306def3cf12646b1fcec.pdf
c0502eb8784489a69ef83e8a9cdbf450.pdf
c05016437edbe79bab0d3269c34155f0.pdf
c04f709d548e9d40b789e5105376449c.pdf
c04e31d6f0f0fc62653a52f929e8eb87.pdf
c04db5117e0c8c3a84ff361d8b2e6cff.pdf
c04d5a144ea0fd326b681d4b222eac6d.pdf
c044f86b41034916b50bdfcbf8686969.pdf
c042acd99d4cafa1781fe3f576da2bcb.pdf
c042431e489eaa89e09e328c9e1e0442.pdf
c04134b7cf8d53ac2419ef26dde6a182.pdf
c040ed1ae7dffad1bb53a08d97a76e71.pdf
c040cffd9bd97a19d9b81ee75d650e75.pdf
c03f0f627d6c76f9dcbaf858e92df2a1.pdf
c03e61cceb8838bfa42b48ad296b3b46.pdf
c03c61846ffcd6cf5a9b93f4371d2daf.pdf
c03a53b87a0896e99ad65311088f2a58.pdf
c039fd16d6ef5b35878cb70e6f465274.pdf
c0370549d66f732610aa8d949d9c6327.pdf
c0361209ecd28be3bb621d073b77a6c4.pdf
c027fd4200f1f16cae6682ef992b6bdc.pdf
c027d8e0a4eb0fc764342da1126a9891.pdf
c0272a4a80055626410166ed1d4b23d0.pdf
c0242fc37b1c5a8a14ffdb6957c7cae2.pdf
c023046badc78367ae37e23022b96b76.pdf
c

b1fb641673f94f8266dd4a035b644ab8.pdf
b1f91c5bffc7d26eaa7f81e672d51cd7.pdf
b1f728939d0b132e51d61c749d336dc5.pdf
b1f59d4624fc571130af656665d954c7.pdf
b1f3ed2fab3c43fe637d6182b67bd0ea.pdf
b1f36141647fdc89c1d0c8ffc2f46495.pdf
b1eeff37323c97da90dea99b2435395a.pdf
b1eadea245c44af490b89ea08aedb8b5.pdf
b1e0b13f6699a46bb9629578b6efea84.pdf
b1e068718d00848271fb1441b621d7e5.pdf
b1dce778bea33d60694073473964b11f.pdf
b1dae09cc13171261570a4ffcb6bc707.pdf
b1d5bdabfd453bc061557ddc60a9931c.pdf
b1d0f6bfac5e887697b2ef26086c9468.pdf
b1ceb9a6f0e15df3b8393ba0432d8ece.pdf
b1cd7b11d9303169c6df40bc3cc4e7aa.pdf
b1cd2fe2f121139c91380cdf265996a6.pdf
b1cd2b7e11c73dce6487412bff0b8144.pdf
b1cd07587462ccdc330dfd88c1a9a9b9.pdf
b1cbefe4d4a252cf8f574c22fe945825.pdf
b1caa14bd6552deb9e8e04af345247c3.pdf
b1ca0658d3c1823f6d6d52a6e8ecbc59.pdf
b1c9407d66e33e6893233b4a6f6125ee.pdf
b1c85c64b59f2ad4df198f36277a083e.pdf
b1c70897cc462f47d44b946b49e279b3.pdf
b1c6687268659e5f794f8959b0ed9035.pdf
b1c60fb3f128a0be464e39a9279bde6f.pdf
b

In [ ]:
import formfyxer